## 10-fold Cross Validation on the Stanik dataset

In [ ]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 9.3 MB/s 
     |████████████████████████████████| 1.3 MB 78.1 MB/s 
     |████████████████████████████████| 1.9 MB 58.2 MB/s 
     |████████████████████████████████| 451 kB 92.5 MB/s 
     |████████████████████████████████| 43 kB 2.3 MB/s 
     |████████████████████████████████| 7.6 MB 52.8 MB/s 
     |████████████████████████████████| 5.5 MB 62.8 MB/s 
     |████████████████████████████████| 10.3 MB 68.6 MB/s 
     |████████████████████████████████| 182 kB 69.0 MB/s 
     |████████████████████████████████| 168 kB 92.1 MB/s 
     |████████████████████████████████| 182 kB 90.9 MB/s 
     |████████████████████████████████| 63 kB 1.6 MB/s 
     |████████████████████████████████| 168 kB 88.5 MB/s 
     |████████████████████████████████| 166 kB 100.5 MB/s 
     |████████████████████████████████| 166 kB 99.3 MB/s 
     |████████████████████████████

In [ ]:
# Import downsampled dataset
df = pd.read_excel('DATASET_downsampled_test1.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Mounted at /content/drive
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [ ]:
# Show the distribution of the labels
print(df['labels'].value_counts())

1    648
3    648
2    648
0    648
Name: labels, dtype: int64


In [ ]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [ ]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'roberta',
    'roberta-base',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/501M [00:00<?, ?B/s]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

Downloading:   0%|          | 0.00/899k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

...

{'mcc': 0.9897060150222423, 'f1': array([0.98333333, 1.        , 0.99115044, 0.99363057]), 'acc': 0.9922779922779923, 'recall': array([0.96721311, 1.        , 1.        , 1.        ]), 'precision': array([1.        , 1.        , 0.98245614, 0.98734177]), 'eval_loss': 0.022313584432457432}
results accuracy [0.8038461538461539, 0.8307692307692308, 0.8648648648648649, 0.8996138996138996, 0.9498069498069498, 0.972972972972973, 0.9613899613899614, 0.9806949806949807, 0.9922779922779923]
Mean-Precision: 0.9173596673596673
results f1:  [array([0.87591241, 0.75757576, 0.90076336, 0.66666667]), array([0.8852459 , 0.82352941, 0.85294118, 0.76190476]), array([0.93877551, 0.85882353, 0.91588785, 0.78321678]), array([0.94594595, 0.86956522, 0.93617021, 0.8245614 ]), array([0.98611111, 0.93442623, 0.97637795, 0.896     ]), array([0.98461538, 0.95867769, 0.99224806, 0.95652174]), array([0.98305085, 0.953125  , 0.97333333, 0.93442623]), array([0.98550725, 0.98529412, 0.99115044, 0.96183206]), array([0

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.989718250793786, 'f1': array([0.99346405, 0.99236641, 1.        , 0.98245614]), 'acc': 0.9922779922779923, 'recall': array([1.        , 1.        , 1.        , 0.96551724]), 'precision': array([0.98701299, 0.98484848, 1.        , 1.        ]), 'eval_loss': 0.01912614447329278}
results accuracy [0.8038461538461539, 0.8307692307692308, 0.8648648648648649, 0.8996138996138996, 0.9498069498069498, 0.972972972972973, 0.9613899613899614, 0.9806949806949807, 0.9922779922779923, 0.9922779922779923]
Mean-Precision: 0.9248514998514998
results f1:  [array([0.87591241, 0.75757576, 0.90076336, 0.66666667]), array([0.8852459 , 0.82352941, 0.85294118, 0.76190476]), array([0.93877551, 0.85882353, 0.91588785, 0.78321678]), array([0.94594595, 0.86956522, 0.93617021, 0.8245614 ]), array([0.98611111, 0.93442623, 0.97637795, 0.896     ]), array([0.98461538, 0.95867769, 0.99224806, 0.95652174]), array([0.98305085, 0.953125  , 0.97333333, 0.93442623]), array([0.98550725, 0.98529412, 0.99115044, 0.96

In [ ]:
print("results accuracy",resultsAcc)
print(f"Mean-accuracy: {sum(resultsAcc) / len(resultsAcc)}")
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.8038461538461539, 0.8307692307692308, 0.8648648648648649, 0.8996138996138996, 0.9498069498069498, 0.972972972972973, 0.9613899613899614, 0.9806949806949807, 0.9922779922779923, 0.9922779922779923]
Mean-accuracy: 0.9248514998514998
results f1:  [array([0.87591241, 0.75757576, 0.90076336, 0.66666667]), array([0.8852459 , 0.82352941, 0.85294118, 0.76190476]), array([0.93877551, 0.85882353, 0.91588785, 0.78321678]), array([0.94594595, 0.86956522, 0.93617021, 0.8245614 ]), array([0.98611111, 0.93442623, 0.97637795, 0.896     ]), array([0.98461538, 0.95867769, 0.99224806, 0.95652174]), array([0.98305085, 0.953125  , 0.97333333, 0.93442623]), array([0.98550725, 0.98529412, 0.99115044, 0.96183206]), array([0.98333333, 1.        , 0.99115044, 0.99363057]), array([0.99346405, 0.99236641, 1.        , 0.98245614])]
results precision:  [array([0.84507042, 0.66666667, 0.9516129 , 0.76923077]), array([0.8852459 , 0.78873239, 0.90625   , 0.75      ]), array([0.88461538, 0.86904762,

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.947923  0.901145  0.975017  0.880503
Average recall     0.965667  0.928924  0.933119  0.874879
Average F1-Score   0.956196  0.913338  0.953002  0.876122

## Testing on the Brunotte dataset

In [ ]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [ ]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [ ]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [ ]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [ ]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise
equal = [None]*np.size(testset['review'])

# Add a column 'equal01' which stores binary values (1 if the two initial labels are equal, 0 otherwise) to calculate the phi-coefficient
equal01 = [None]*np.size(testset['review'])

# Add a column 'labeled_correctly01' which stores binary values (1 if the model correctly labeled the text, 0 otherwise) to calculate the phi-coefficient
labeled_correctly01 = [None]*np.size(testset['review'])

# Add a column 'prediction' which contains the model's predictions
prediction = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset['label 1'], testset['label 2']):
  if(label1 == label2):
    equal[i] = True
    equal01[i] = 1
  else:
    equal[i] = False
    equal01[i] = 0
  i += 1
  
testset['equal'] = equal

In [ ]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

# counter to go through all the reviews and fill the column 'labeled_correctly' with true if they have been labeled correctly, and false if not
i = 0

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
    prediction[i] = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
    prediction[i] = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
    prediction[i] = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'
    prediction[i] = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

  if label == predicted_label:
    labeled_correctly01[i] = 1
  else:
    labeled_correctly01[i] = 0
  i+=1

testset['labeled_correctly'] = labeled_correctly01
testset['prediction'] = prediction

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
testset.to_excel("Brunotte_with_predictions_test1_roberta.xlsx")  

In [ ]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   73.67 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 78.67 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   44.77 %,  n =  239


In [ ]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.9010204081632653
Precision D:  0.3515981735159817
Precision I:  0.42857142857142855
Precision P:  0.5576923076923077
Recall B:  0.8012704174228675
Recall D:  0.8105263157894737
Recall I:  0.1
Recall P:  0.5873417721518988
F1-score B:  0.8482228626320846
F1-score D:  0.4904458598726114
F1-score I:  0.16216216216216217
F1-score P:  0.5721331689272503


In [ ]:
# Calculates the phi-coefficient of the labels being predicted correctly and the researchers being 

print('MCC for initial agreement of raters and correct or false labeling',matthews_corrcoef(labeled_correctly01, equal01))

MCC for initial agreement of raters and correct or false labeling 0.2728398524964205


## 10-fold Cross Validation on a combination of the Stanik dataset and the Brunotte dataset

In [ ]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('DATASET_Trainingskorpus_combined_test1.xlsx')

df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [ ]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

2    743
0    743
1    743
3    743
Name: labels, dtype: int64


In [ ]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'roberta',
    'roberta-base',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-accuracy: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.7714587774479886, 'f1': array([0.8852459 , 0.80446927, 0.89041096, 0.75167785]), 'acc': 0.8288590604026845, 'recall': array([0.9       , 0.84705882, 0.84415584, 0.73684211]), 'precision': array([0.87096774, 0.76595745, 0.94202899, 0.76712329]), 'eval_loss': 0.4560399055480957}
results accuracy [0.8288590604026845]
Mean-accuracy: 0.8288590604026845
results f1:  [array([0.8852459 , 0.80446927, 0.89041096, 0.75167785])]
results precision:  [array([0.87096774, 0.76595745, 0.94202899, 0.76712329])]
results recall:  [array([0.9       , 0.84705882, 0.84415584, 0.73684211])]


...

{'mcc': 0.977432859536004, 'f1': array([0.99186992, 0.99447514, 0.96453901, 0.97986577]), 'acc': 0.9831649831649831, 'recall': array([0.98387097, 0.98901099, 0.97142857, 0.98648649]), 'precision': array([1.        , 1.        , 0.95774648, 0.97333333]), 'eval_loss': 0.10088171300135161}
results accuracy [0.8288590604026845, 0.9026845637583892, 0.9393939393939394, 0.936026936026936, 0.9696969696969697, 0.9797979797979798, 0.9865319865319865, 0.9797979797979798, 0.9831649831649831]
Mean-accuracy: 0.945106044285761
results f1:  [array([0.8852459 , 0.80446927, 0.89041096, 0.75167785]), array([0.94047619, 0.88157895, 0.94573643, 0.84353741]), array([0.96969697, 0.89655172, 0.95483871, 0.92405063]), array([0.96402878, 0.9112426 , 0.99328859, 0.87591241]), array([0.96610169, 0.95714286, 0.99421965, 0.95705521]), array([0.98863636, 0.97744361, 0.99300699, 0.95774648]), array([0.98591549, 0.984375  , 0.99401198, 0.98089172]), array([1.        , 0.97175141, 0.99224806, 0.94339623]), array([0.991

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.9910139453709021, 'f1': array([0.99363057, 0.99236641, 1.        , 0.98780488]), 'acc': 0.9932659932659933, 'recall': array([1.        , 0.98484848, 1.        , 0.98780488]), 'precision': array([0.98734177, 1.        , 1.        , 0.98780488]), 'eval_loss': 0.04880394904237045}
results accuracy [0.8288590604026845, 0.9026845637583892, 0.9393939393939394, 0.936026936026936, 0.9696969696969697, 0.9797979797979798, 0.9865319865319865, 0.9797979797979798, 0.9831649831649831, 0.9932659932659933]
Mean-accuracy: 0.9499220391837842
results f1:  [array([0.8852459 , 0.80446927, 0.89041096, 0.75167785]), array([0.94047619, 0.88157895, 0.94573643, 0.84353741]), array([0.96969697, 0.89655172, 0.95483871, 0.92405063]), array([0.96402878, 0.9112426 , 0.99328859, 0.87591241]), array([0.96610169, 0.95714286, 0.99421965, 0.95705521]), array([0.98863636, 0.97744361, 0.99300699, 0.95774648]), array([0.98591549, 0.984375  , 0.99401198, 0.98089172]), array([1.        , 0.97175141, 0.99224806, 0.94

In [ ]:
print("results accuracy",resultsAcc2)
print(f"Mean-accuracy: {sum(resultsAcc2) / len(resultsAcc2)}")
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.8288590604026845, 0.9026845637583892, 0.9393939393939394, 0.936026936026936, 0.9696969696969697, 0.9797979797979798, 0.9865319865319865, 0.9797979797979798, 0.9831649831649831, 0.9932659932659933]
Mean-accuracy: 0.9499220391837842
results f1:  [array([0.8852459 , 0.80446927, 0.89041096, 0.75167785]), array([0.94047619, 0.88157895, 0.94573643, 0.84353741]), array([0.96969697, 0.89655172, 0.95483871, 0.92405063]), array([0.96402878, 0.9112426 , 0.99328859, 0.87591241]), array([0.96610169, 0.95714286, 0.99421965, 0.95705521]), array([0.98863636, 0.97744361, 0.99300699, 0.95774648]), array([0.98591549, 0.984375  , 0.99401198, 0.98089172]), array([1.        , 0.97175141, 0.99224806, 0.94339623]), array([0.99186992, 0.99447514, 0.96453901, 0.97986577]), array([0.99363057, 0.99236641, 1.        , 0.98780488])]
results precision:  [array([0.87096774, 0.76595745, 0.94202899, 0.76712329]), array([0.91860465, 0.87012987, 0.93846154, 0.88571429]), array([0.96385542, 0.86666667,

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.965522  0.925540  0.979803  0.929167
Average recall     0.971846  0.950076  0.965330  0.912229
Average F1-Score   0.968560  0.937140  0.972230  0.920194